<a href="https://colab.research.google.com/github/meiaalsup/lda_infographics/blob/master/6_804.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

6.804 Final Project

Meia Alsup, Sravya Bhamidipati, Anelise Newman

In [56]:
from string import digits
import json
import pickle as pkl
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from IPython.display import Image, display
from IPython.core.display import HTML 
import urllib.request as request

from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaModel
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
from nltk.corpus import wordnet

In [3]:
import nltk

In [26]:
f = open('raw_ocr_output.pickle','rb')
ocr = pkl.load(f)
f.close()

In [27]:
less_ocr = {key: ocr[key] for i, key in enumerate(ocr) if i < 100}
less_ocr

{'the-ultimate-guide-to-using-powerpoint-effectively_521e33ea8b189.jpg': [("THE ULTIMATE GUIDE TO\nUSING POWERPOINT EFFECTIVELY\n(from your friends at Cubicle Ninjas)\nAt Cubicle Ninjas, we understand that the foundation of successful design is\nclear communication. This applies nowhere more strongly than the humble\nPowerPoint presentation. PowerPoint provides an extremely powerful and\neffective platform for storytelling. Yet it's also easy to communicate poorly with\nPowerPoint. Follow our advice and you'll be a PowerPoint pro in no time!\n1. PLANNING\n2. DESIGN\n3. EXECUTION\nTHE PLANNING PROCESS\nBefore you begin, figure out what story you\nneed to tell, and condense that story down\nto its most powerful and relevant elements.\nUnderstand\nyour audience.\nList your\nkey points\nKeep it\nsimple!\nTHE DESIGN PROCESS\nHere are three distinct design methodologies,\nfrom three of our generation's most effective\nstorytellers. Learn from their advice!\nSTEVE JOBS\nTIP 1:\nTIP 1:\nTIP 2:

In [60]:
#f = open('icon_annotations_testing.pickle','rb')
#icons = pkl.load(f)
#f.close()

In [76]:
# annotations from task where participants marked bounding boxes around all icons on an infographic
icon_dict = pkl.load(open( "icon_annotations_all.pickle", "rb") )

FileNotFoundError: [Errno 2] No such file or directory: 'icon_annotations_all.pickle'

In [62]:
len(icon_dict)

1000

In [64]:
icons

{'learning-japanese-steps-to-success--fluency_502914cd97c3e.png': [{'top': 0.8996269656897784,
   'left': 0.44583333333333336,
   'right': 0.446875,
   'bottom': 0.8999843638313081},
  {'top': 0.8996269656897784,
   'left': 0.44583333333333336,
   'right': 0.5333333333333333,
   'bottom': 0.9217856504646176},
  {'top': 0.9021287526804861,
   'left': 0.5885416666666666,
   'right': 0.6260416666666667,
   'bottom': 0.9164246783416726},
  {'top': 0.8999843638313081,
   'left': 0.68125,
   'right': 0.778125,
   'bottom': 0.9228578448892065},
  {'top': 0.9057027340957827,
   'left': 0.30416666666666664,
   'right': 0.3375,
   'bottom': 0.9235726411722659},
  {'top': 0.9821859363831308,
   'left': 0.8052083333333333,
   'right': 0.8395833333333333,
   'bottom': 0.9929078806290207},
  {'top': 0.9818285382416011,
   'left': 0.8479166666666667,
   'right': 0.88125,
   'bottom': 0.9918356862044317},
  {'top': 0.6887620621872766,
   'left': 0.053125,
   'right': 0.071875,
   'bottom': 0.693765636

In [67]:
icons_english  = set(icons.keys())
icons_english

{'removal-of-cactus-spines-from-the-skin--rei_502917ef54082.jpg',
 'worlds-largest-aircraft_50290a5d97cad.png',
 'how-to-design-your-business-card-with-psychology-in-mind-infographic_50f6e0bb07905.jpg',
 'build-your-wardrobe-from-the-ground-up--wardrobe-essentials-for-men_519b35f55063d.jpg',
 'academic-clinics-guide-to-the-upcat_502914389cbff.jpg',
 'small-meals-5-times-a-day_5029117fa696c.jpg',
 'female-body-image_502910e3a70ae.jpg',
 '2013-halloween-costumes-pop-culture-favorites_52600dc02a6d2.jpg',
 'how-many-calories-do-you-burn-at-work_510a5448ee3c0.png',
 'essential-vitamins-and-minerals_5130deadc1bc1.png',
 'who-is-the-most-annoying-facebook-user_5029150ce1260.jpg',
 'how-startup-funding-works_51db987f390b4.png',
 'celebrating-egyptian-entrepreneurs_50290d56bf990.png',
 'icebergs_5154ccc467118.png',
 'the-caffeine-poster-how-much-caffeine-are-you-drinking_50290a6d5a6df.jpg',
 'degrees-in-early-childhood-education--2014-emerging-trends_53e1513780eb3.jpg',
 'the-growth-of-distance

In [6]:
NUM_TOPICS = 30

In [7]:

f = open('google_text_extraction_output.pckl','rb')
infographic_name_to_words = pkl.load(f)
f.close()

print('We have extracted words from %d infographics.'%len(infographic_name_to_words))

We have extracted words from 62361 infographics.


In [8]:
def contains_english(set_of_words):
    english = set(['the', 'she', 'different', 'time', 'and', 'client', 'sports', 'grammar', 'family', 'report'])
    spanish = set(['el', 'es', 'cuando', 'esta', 'malo', 'que', 'tiene', 'para'])
    if bool(set(set_of_words) & spanish):
        return False
    if bool(set(set_of_words) & english):
        return True
    return False

In [9]:
english  = {key: val for key, val in infographic_name_to_words.items() if contains_english(val)}
len(english)

46952

In [25]:
english.keys()

dict_keys(['free-autism-infographic_564c4ed54ea8f.jpg', 'lemonlys-one-sweet-year-2012-annual-report_51141ef25ba83.jpg', 'top-10-darkest-characters-in-film_544fde05817b7.jpg', '12-christmas-traditions-from-around-the-world_50290c852911e.jpg', 'dc-power-on-board-lowering-environmental-impact_5029160e8b05c.png', 'common-health-issues-veterans-face_5385e1a9af293.jpg', '6-classic-coat-styles-for-men_5306499534889.jpg', 'interesting-facts-about-teeth_53d291913ac5f.jpg', 'databagg--online-storage-service_53cf95209c581.jpg', 'diabetes-month-an-infographic_52791b9fc14d8.jpg', 'how-strong-is-your-password_5069f9e75a9af.jpg', 'to-print-or-not-to-print_502911b1e767d.jpg', 'the-most-influential-legal-cases-of-the-last-century_5029118e0fe8b.png', 'what-do-you-think-about-sopa-and-pipa_5029165112c1d.jpg', 'social-costs_527ab889b8867.jpg', 'leadership-and-hierarchy-in-hospitals_544abe224a03e.jpg', 'wedding-cake_5444a4e15a486.jpg', 'water-is-not-a-natural-resource_544e8498978d6.jpg', 'tips-for-successf

In [11]:
#json.dump(english, open('filtered.json', 'w'))
#json.dump([key for key, val in english.items()], open('filtered_keys.json', 'w'))

In [19]:
words = [list_words for list_words in english.values()]
newList = []
stemmer = PorterStemmer()
for wordList in words:
    thisList = []
    for word in wordList:
        if len(word) > 2 and word.isalpha() and word not in STOPWORDS and wordnet.synsets(word):
            thisList.append(word.lower())
            #thisList.append(stemmer.stem(WordNetLemmatizer().lemmatize(word.lower(), pos='v')))
    newList.append(thisList)

In [20]:
len(newList)

46952

In [21]:
# Create a corpus from a list of texts
common_dictionary = Dictionary(newList)
common_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=10000)

common_corpus = [common_dictionary.doc2bow(text) for text in newList]
# Train the model on the corpus.
id2token = {val:key for key, val in common_dictionary.token2id.items()}

In [22]:
# Train the model on the corpus.
lda = LdaModel(common_corpus, num_topics=NUM_TOPICS)

In [23]:
for i in range(NUM_TOPICS):
    terms = lda.get_topic_terms(i, 20)
    print(f'Topic number {i}')
    val = {id2token[t[0]]: t[1] for t in terms}
    #print(f'Top 20 terms: {val}')
    print(f'Top 20 terms: {val.keys()}')

Topic number 0
Top 20 terms: dict_keys(['teeth', 'dental', 'waste', 'air', 'natural', 'plastic', 'tooth', 'plants', 'water', 'damage', 'cosmetic', 'cause', 'tons', 'chemical', 'plant', 'chemicals', 'soil', 'bacteria', 'species', 'use'])
Topic number 1
Top 20 terms: dict_keys(['game', 'games', 'players', 'team', 'won', 'win', 'sports', 'season', 'player', 'league', 'play', 'football', 'winning', 'final', 'cup', 'wins', 'gas', 'teams', 'points', 'super'])
Topic number 2
Top 20 terms: dict_keys(['travel', 'city', 'london', 'new', 'hotel', 'park', 'miles', 'time', 'york', 'beach', 'first', 'trip', 'year', 'flight', 'top', 'travelers', 'bowl', 'island', 'airlines', 'all'])
Topic number 3
Top 20 terms: dict_keys(['million', 'world', 'billion', 'united', 'energy', 'countries', 'south', 'total', 'population', 'global', 'china', 'north', 'year', 'states', 'years', 'number', 'america', 'country', 'largest', 'oil'])
Topic number 4
Top 20 terms: dict_keys(['president', 'members', 'vote', 'new', 'p

In [24]:
saved = lda.save('saved_lda_30_topics')

In [36]:
list(english.keys())[:10]

['free-autism-infographic_564c4ed54ea8f.jpg',
 'lemonlys-one-sweet-year-2012-annual-report_51141ef25ba83.jpg',
 'top-10-darkest-characters-in-film_544fde05817b7.jpg',
 '12-christmas-traditions-from-around-the-world_50290c852911e.jpg',
 'dc-power-on-board-lowering-environmental-impact_5029160e8b05c.png',
 'common-health-issues-veterans-face_5385e1a9af293.jpg',
 '6-classic-coat-styles-for-men_5306499534889.jpg',
 'interesting-facts-about-teeth_53d291913ac5f.jpg',
 'databagg--online-storage-service_53cf95209c581.jpg',
 'diabetes-month-an-infographic_52791b9fc14d8.jpg']

In [58]:
base= 'http://thumbnails.visually.netdna-cdn.com'
for url_ in list(english.keys())[30:150]:
    display(Image(url=f'{base}/{url_}'))
    request.urlretrieve(f'{base}/{url_}', f'images/{url_}')


In [68]:
intersection = set([url_ for url_ in english.keys() if url_ in icons_english])

In [72]:
intersection

{'10-blog-titles-that-drive-massive-traffic_52556385135e3.jpg',
 '10-commonly-misunderstood-words-in-english_50290cfa6c279.jpg',
 '10-exotic-destination-vacations_50290aa5225d2.jpg',
 '10-facts-about-hunger-in-america_5029110c3b0fd.jpg',
 '10-iphone-fun-facts_502918c495ab8.jpg',
 '10-little-known-facts-about-clownfish_5300516e128a5.jpg',
 '10-mobile-marketing-statistics_5261274b6729b.jpg',
 '10-most-common-car-insurance-myths_502918d424c9f.jpg',
 '10-signs-you-are-truly-happy_502919961ffb2.jpeg',
 '10-surefire-ways-on-how-to-lose-body-fat-fast_553a84af09d60.jpg',
 '12-mental-benefits-of-exercise_513517b4b5df5.jpg',
 '12-month-wedding-checklist-for-the-bride--groom_51891830823b2.jpg',
 '12-most-dangerous-cars-of-all-time_5166e90360a94.png',
 '12-stages-of-selling-your-website_51361a3535024.jpg',
 '12-tips-on-staying-inspired_51baeeaa1b15c.jpg',
 '12-ways-to-christmas-in-july-with-artificial-christmas-trees_5217d2e89b715.png',
 '13-oil-spills-in-30-days_516ff2b7d2988.jpg',
 '15-celebs-wi

In [73]:
for url_ in intersection:
    display(Image(url=f'{base}/{url_}'))
    request.urlretrieve(f'{base}/{url_}', f'images/{url_}')

KeyboardInterrupt: 